In [1]:
from fnmatch import fnmatch
from PIL import Image
from PIL import ImageFile
from pathlib import Path
from shutil import copyfile

import imagehash
import mysql.connector
import os
import re

In [4]:
# GENERAL CONFIGS

ImageFile.LOAD_TRUNCATED_IMAGES = True

# == Files config ==
MAIN_FOLDER = r"D:\images\_outlaw"

# == Database config ==
conn = mysql.connector.connect(
  host="localhost",
  user="root",
  password="root"
)

cursor = conn.cursor(buffered=True)

DB_NAME = "blp_dataset"
TABLE_NAME = "products_tmp_outlaw"

cursor.execute("USE {}".format(DB_NAME))

## First step: clear all repeated images

Using Perceptual Hashing (P-Hash) algorithm, we analyze and remove all images that have equal hashes.
We also updated the database, so we can have control over how the Dark Marketplace (DM) data was distributed. This can also help with future work.

Database fields that do not have a valid image will not be used in the training. We will only use those products that have both description and title as well as image, and vice versa, in order to maintain a balance between the results of the two networks.

Keeping the lines in the database that have no image, just placing a flag to indicate the status, we open the possibility of using this data in training, if necessary.

Also, we will copy the images that are not repeated, but has the texts into this situation, so we can use those files if necessary.

In [ ]:
## CLEAR REPEATED IMAGES
Image.MAX_IMAGE_PIXELS = None

MAIN_FOLDER = r"D:\images\_bbm"
folder = Path(MAIN_FOLDER)
p_img_hashes = {}
error_files = []
total_rem = 0

for image in os.listdir(folder):
    image_path = Path(f"{folder}\{image}")

    try:
        hash = imagehash.phash(Image.open(image_path))
        image_name = os.path.splitext(image)[0]

        if hash in p_img_hashes:
            print(image_path)
            os.remove(image_path)
            
            total_rem = total_rem + 1
        else:
            p_img_hashes[hash] = image
    except:
        error_files.append(image)

In [6]:
def del_image(image_path):
    os.remove(image_path)

In [2]:
def copy_image(name):
    url_image = Path(f"{Path(MAIN_FOLDER)}\{name}.jpeg")
    dst_dir = Path(f"D:\images\excluded_product\{name}.jpeg")

    if url_image.exists():
        copyfile(url_image, dst_dir)
        del_image(url_image)

In [4]:
# CLEAR REPEATED TEXTS
cursor.execute(
    "SELECT description, COUNT(description) "
    "FROM products_tmp_outlaw "
    "GROUP BY description HAVING COUNT(description) > 1")

repeated = cursor.fetchall()

for res in repeated:
    cursor.execute("SELECT id FROM " + TABLE_NAME + " WHERE description = %s", (res[0],))
    to_clear = cursor.fetchall()
    cont = 0

    for item in to_clear:
        if cont > 0:
            print(f"Product {item[0]}")

            cursor.execute("DELETE FROM " + TABLE_NAME + " WHERE id = %s", (item[0],))
            conn.commit()
        else:
            print(f"Product {item[0]} saved")
        cont = cont + 1

Product 4 saved
Product 5001
Product 15292
Product 15350
Product 15755
Product 5 saved
Product 1561
Product 1563
Product 1566
Product 1581
Product 1716
Product 1925
Product 2060
Product 2111
Product 2119
Product 2185
Product 2273
Product 2274
Product 2307
Product 2500
Product 2716
Product 2765
Product 2995
Product 3043
Product 3166
Product 3416
Product 3596
Product 3603
Product 3632
Product 3723
Product 3783
Product 3858
Product 3880
Product 4021
Product 4060
Product 4430
Product 4868
Product 4948
Product 5981
Product 6446
Product 6672
Product 6674
Product 6677
Product 6692
Product 6717
Product 6812
Product 6882
Product 6925
Product 6957
Product 7058
Product 7215
Product 7241
Product 7335
Product 7380
Product 7734
Product 7820
Product 7867
Product 8162
Product 8366
Product 8537
Product 8848
Product 9018
Product 9120
Product 9265
Product 9531
Product 9547
Product 10697
Product 10916
Product 11077
Product 11662
Product 11664
Product 11667
Product 11682
Product 11778
Product 12153
Product

Product 183207
Product 183662
Product 183920
Product 184011
Product 184014
Product 184015
Product 184016
Product 184464
Product 184517
Product 184574
Product 184743
Product 184757
Product 184868
Product 185017
Product 185051
Product 185080
Product 185092
Product 185146
Product 185321
Product 185370
Product 185403
Product 185539
Product 185614
Product 185664
Product 185828
Product 185874
Product 185883
Product 185913
Product 186103
Product 186134
Product 186331
Product 186412
Product 186414
Product 186523
Product 186671
Product 186702
Product 186711
Product 187399
Product 187439
Product 187521
Product 187544
Product 187832
Product 188317
Product 188339
Product 188916
Product 188919
Product 188920
Product 188921
Product 189073
Product 189536
Product 189751
Product 189915
Product 190103
Product 190397
Product 190620
Product 190704
Product 190762
Product 190790
Product 190841
Product 190844
Product 190946
Product 191041
Product 191061
Product 191073
Product 191123
Product 191189
Product 19

Product 269746
Product 269807
Product 271039
Product 271381
Product 271384
Product 271385
Product 271386
Product 271505
Product 271537
Product 271833
Product 272479
Product 272513
Product 272606
Product 272621
Product 272645
Product 272723
Product 272816
Product 272849
Product 272959
Product 272984
Product 273099
Product 273155
Product 273353
Product 273404
Product 273519
Product 273833
Product 273932
Product 274725
Product 274879
Product 275628
Product 275641
Product 275805
Product 275831
Product 276223
Product 276226
Product 276227
Product 276228
Product 276378
Product 276511
Product 277912
Product 278156
Product 278228
Product 278238
Product 278260
Product 278570
Product 278638
Product 278733
Product 278781
Product 278816
Product 278938
Product 279210
Product 281193
Product 281196
Product 281197
Product 281198
Product 281350
Product 286152
Product 286155
Product 286156
Product 286157
Product 286309
Product 290976
Product 290979
Product 290980
Product 290981
Product 291118
Product 29

Product 14349
Product 14377
Product 14636
Product 14859
Product 16549
Product 16550
Product 16551
Product 16552
Product 16553
Product 16555
Product 16556
Product 16557
Product 25704
Product 25705
Product 25706
Product 25707
Product 25708
Product 25710
Product 25711
Product 25712
Product 30649
Product 30650
Product 30651
Product 30652
Product 30653
Product 30655
Product 30656
Product 30657
Product 33580
Product 33581
Product 33582
Product 33583
Product 33584
Product 33586
Product 33587
Product 33588
Product 38564
Product 38565
Product 38566
Product 38567
Product 38568
Product 38570
Product 38571
Product 38572
Product 43551
Product 43552
Product 43553
Product 43554
Product 43555
Product 43557
Product 43558
Product 43559
Product 48538
Product 48539
Product 48540
Product 48541
Product 48542
Product 48544
Product 48545
Product 48546
Product 53522
Product 53523
Product 53524
Product 53525
Product 53526
Product 53528
Product 53529
Product 53530
Product 58471
Product 58472
Product 58473
Produc

Product 121607
Product 121691
Product 122065
Product 122103
Product 122202
Product 122313
Product 122756
Product 123013
Product 123014
Product 123015
Product 123016
Product 123017
Product 123019
Product 123020
Product 123021
Product 123114
Product 123801
Product 123808
Product 123811
Product 123817
Product 123877
Product 123964
Product 123998
Product 124000
Product 124016
Product 124055
Product 124111
Product 124197
Product 124226
Product 124316
Product 124320
Product 124451
Product 124470
Product 124532
Product 124611
Product 124673
Product 124694
Product 124695
Product 124848
Product 124856
Product 124910
Product 124926
Product 124953
Product 124966
Product 125077
Product 125079
Product 125112
Product 125185
Product 125194
Product 125390
Product 125536
Product 125550
Product 125565
Product 125590
Product 125592
Product 125606
Product 125660
Product 125663
Product 125725
Product 125816
Product 125833
Product 125927
Product 125941
Product 126099
Product 126137
Product 126340
Product 12

...

Product 327509
Product 331210
Product 333824
Product 335006
Product 336442
Product 336794
Product 342457
Product 343513
Product 343832
Product 345220
Product 346281
Product 346617
Product 347036
Product 347476
Product 347915
Product 349022
Product 349054
Product 350074
Product 350184
Product 351182
Product 352259
Product 324525 saved
Product 326397
Product 327297
Product 324655 saved
Product 324977
Product 326714
Product 327025
Product 327037
Product 327589
Product 329465
Product 333281
Product 337207
Product 338153
Product 338558
Product 338797
Product 340732
Product 344550
Product 347240
Product 347744
Product 349206
Product 349215
Product 349343
Product 349479
Product 350418
Product 351865
Product 352102
Product 326388 saved
Product 326389
Product 327448
Product 327544
Product 327583
Product 327948
Product 328801
Product 329249
Product 331195
Product 331196
Product 333058
Product 333744
Product 333784
Product 334991
Product 334992
Product 335145
Product 335285
Product 335692
Product

Product 332194 saved
Product 334616
Product 335216
Product 335546
Product 336147
Product 338218
Product 338839
Product 341436
Product 342082
Product 343498
Product 344537
Product 344729
Product 345311
Product 345892
Product 349806
Product 351890
Product 352375
Product 332195 saved
Product 332318
Product 332708
Product 333134
Product 334737
Product 335072
Product 335075
Product 335076
Product 335077
Product 335339
Product 335476
Product 335555
Product 335644
Product 336052
Product 336081
Product 336213
Product 336218
Product 336705
Product 337079
Product 338402
Product 338608
Product 338807
Product 339218
Product 339354
Product 339409
Product 339673
Product 339821
Product 339847
Product 341315
Product 342133
Product 344614
Product 344923
Product 345941
Product 346366
Product 346369
Product 346370
Product 346371
Product 346444
Product 346564
Product 346607
Product 346625
Product 347313
Product 347487
Product 347506
Product 348008
Product 349602
Product 350946
Product 351267
Product 35127

Product 339171
Product 339426
Product 339964
Product 340188
Product 340297
Product 342511
Product 342513
Product 342517
Product 342518
Product 342579
Product 342715
Product 343013
Product 343959
Product 344155
Product 344274
Product 344917
Product 344999
Product 345307
Product 345316
Product 346335
Product 346337
Product 346341
Product 346342
Product 346555
Product 346700
Product 346809
Product 347258
Product 347291
Product 347582
Product 348988
Product 349198
Product 349240
Product 351236
Product 351238
Product 351242
Product 351243
Product 351609
Product 351995
Product 352046
Product 352183
Product 352776
Product 352848
Product 333690 saved
Product 333989
Product 334747
Product 335045
Product 336191
Product 336982
Product 337315
Product 338391
Product 342057
Product 342496
Product 343196
Product 343249
Product 346043
Product 346320
Product 347072
Product 347133
Product 350020
Product 350687
Product 351221
Product 351517
Product 352092
Product 352185
Product 333734 saved
Product 33375

Product 337429 saved
Product 339646
Product 340774
Product 346422
Product 346479
Product 347558
Product 349977
Product 351324
Product 351381
Product 351773
Product 337634 saved
Product 337878
Product 339469
Product 341880
Product 343734
Product 343811
Product 344322
Product 346092
Product 346386
Product 346387
Product 346811
Product 347300
Product 349053
Product 350012
Product 350664
Product 351288
Product 351289
Product 351594
Product 353050
Product 353054
Product 337651 saved
Product 338469
Product 338948
Product 340550
Product 342515
Product 346339
Product 346557
Product 346711
Product 346927
Product 347077
Product 350918
Product 351240
Product 337896 saved
Product 337919
Product 338789
Product 339119
Product 339136
Product 340353
Product 341234
Product 343692
Product 343716
Product 343799
Product 344174
Product 344465
Product 344943
Product 345237
Product 346023
Product 346399
Product 346400
Product 346401
Product 346402
Product 346451
Product 346830
Product 347480
Product 347676
P

Product 343575 saved
Product 345258
Product 346529
Product 347042
Product 348055
Product 351432
Product 352036
Product 343585 saved
Product 346522
Product 347022
Product 347407
Product 347485
Product 347517
Product 348281
Product 348594
Product 349340
Product 351425
Product 351885
Product 352258
Product 343705 saved
Product 346458
Product 347287
Product 347740
Product 348535
Product 351360
Product 352001
Product 353011
Product 343740 saved
Product 346533
Product 347277
Product 348416
Product 349210
Product 351436
Product 344026 saved
Product 344312
Product 346525
Product 346953
Product 347225
Product 347428
Product 349083
Product 349448
Product 349964
Product 350155
Product 351428
Product 345091 saved
Product 346535
Product 346621
Product 346850
Product 346894
Product 350231
Product 351438
Product 351937
Product 345260 saved
Product 346530
Product 346633
Product 347438
Product 349321
Product 349618
Product 351433
Product 351500
Product 352251
Product 345417 saved
Product 346534
Product

## Next step: join the data

In [7]:
cursor.execute("SELECT id, name, description, market_name, seller_name, illegal FROM products_tmp_outlaw")
items = cursor.fetchall()

DEST_FOLDER = r"D:\images\illegal"
dest = Path(DEST_FOLDER)

error = []

for i in items:
    query = "INSERT INTO products (name, description, market_name, seller_name, illegal) VALUES (%s, %s, %s, %s, %s)"
    values = (i[1], i[2], i[3], i[4], "t")

    cursor.execute(query, values)
    conn.commit()
    product_id = cursor.lastrowid

    url_image = Path(f"{Path(MAIN_FOLDER)}\{i[0]}.jpeg")
    dst_dir = Path(f"{Path(dest)}\{product_id}.jpeg")

    if url_image.exists():
        copyfile(url_image, dst_dir)
        del_image(url_image)
        
    else:
        error.append(i[0])